In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import *
from pyspark.sql.types import *
from pyspark.sql.window import Window

In [0]:
%fs
ls "/mnt/silverData"

path name size modificationTime dbfs:/mnt/silverData/cleaned-data/ cleaned-data/ 0 1731045331000 dbfs:/mnt/silverData/input/ input/ 0 1730977215000 dbfs:/mnt/silverData/processed-data/ processed-data/ 0 1731045341000

In [0]:
cleanData_df = spark.read.format("delta").load("/mnt/silverData/cleaned-data/")

In [0]:
display(cleanData_df)

Transaction_ID Customer_ID Name Email Phone Address City State Zipcode Country Age Gender Income Customer_Segment Date Year Month Time Total_Purchases Amount Total_Amount Product_Category Product_Brand Product_Type Feedback Shipping_Method Payment_Method Order_Status Ratings products Quarter 3970929 44255 Marcia Koch Lisa69@gmail.com 9080277931 8690 Oconnell Crescent Adelaide New South Wales 45373 Australia 46 Male Medium New 2023-08-20 2023 AUGUST 15:12:29 5.0 168.4952294 842.48 Grocery Coca-Cola Water Average Express Debit Card Shipped 2 Spring water 3 9797885 83532 Matthew Mills Brian46@gmail.com 2497854804 081 Whitney Summit Suite 178 Adelaide New South Wales 19137 Australia 46 Female Low New null 2023 AUGUST 20:57:13 3.0 217.6162425 652.85 Grocery Nestle Snacks Excellent Standard PayPal Delivered 4 Fruit snacks 3 9802394 28806 Jennifer Sullivan Bruce49@gmail.com 5098632200 13898 Carson Tunnel Suite 085 Adelaide New South Wales 49136 Australia 19 Female Low New 2023-04-23 2023 APRIL 13:29:36 1.0 220.256694 220.26 Home Decor Bed Bath & Beyond Bedding Bad Express Debit Card Delivered 1 Dust ruffle 2 8380102 69115 Tracy Stephens Kelly43@gmail.com 8769915260 8833 Flores Radial Adelaide New South Wales 79425 Australia 41 Male Medium New null 2023 NOVEMBER 6:52:40 6.0 34.55794551 207.35 Grocery Pepsi Juice Excellent Express Credit Card Delivered 4 Orange juice 4 1463629 77283 Darrell Newman Carolyn68@gmail.com 8137077759 826 Samantha Lock Apt. 856 Adelaide New South Wales 62683 Australia 70 Male Low New 2023-05-26 2023 MAY 7:17:41 5.0 271.581204 1357.91 Grocery Nestle Coffee Good Express Credit Card Pending 3 Instant coffee 2 5128396 73947 Breanna Lowe Dylan5@gmail.com 2346579502 89470 Jorge Crossing Suite 384 Adelaide New South Wales 97697 Australia 46 Male Low New 2023-08-15 2023 AUGUST 1:17:01 5.0 82.5955648 412.98 Home Decor IKEA Decorations Good Standard Credit Card Delivered 4 Mirrors 3 4250512 87350 Ashley Armstrong Nathan18@gmail.com 9860363644 841 Welch Pike Adelaide New South Wales 73234 Australia 40 Male Low New 2023-12-23 2023 DECEMBER 13:21:29 7.0 16.76277446 117.34 Grocery Coca-Cola Soft Drink Average Express Debit Card Shipped 2 Fruit punch 4 2879484 76573 Madeline Pratt Richard46@gmail.com 4439366081 0082 Durham Coves Suite 183 Adelaide New South Wales 91232 Australia 22 Male Low New null 2023 SEPTEMBER 6:14:42 10.0 254.5369921 2545.37 Books Penguin Books Children's Average Same-Day Credit Card Processing 2 Educational kits 3 1350714 15861 Nicole Woods Barbara90@gmail.com 4317007993 17257 Foster Ridges Belfast England 58188 UK 22 Female Low Regular null 2023 JULY 17:50:26 9.0 41.68210074 375.14 Grocery Nestle Chocolate Average Standard PayPal Delivered 2 Dark chocolate 3 5127937 45915 Melissa Pace Rachel8@gmail.com 5853514125 1372 Kyle Branch Suite 002 Belfast England 56727 UK 20 Male Low New 2023-10-13 2023 OCTOBER 21:27:02 6.0 441.420632 2648.52 Grocery Nestle Chocolate Excellent Express PayPal Delivered 4 Chocolate-covered fruits 4 9214368 49898 Dana Harvey Samantha26@gmail.com 3157698105 8963 David Center Suite 662 Belfast England 69780 UK 20 Female Low Regular null 2023 APRIL 0:29:29 8.0 422.1476917 3377.18 Books HarperCollins Thriller Average Standard Cash Pending 2 Adventure 2 4899893 98806 Victor Stevens Wendy46@gmail.com 2184424997 47383 Dwayne Crossroad Belfast England 38159 UK 50 Male Medium Regular null 2023 JULY 16:39:57 3.0 425.3956396 1276.19 Grocery Pepsi Water Bad Express Credit Card Shipped 1 Coconut water 3 6714805 79288 Brittany Grant Lucas22@gmail.com 1363169533 52381 Elizabeth Drive Apt. 504 Belfast England 6182 UK 29 Female High Premium null 2023 JUNE 18:45:25 3.0 455.3924426 1366.18 Clothing Adidas Shoes Average Express PayPal Processing 2 Sneakers 2 8208801 76339 Samuel Lee Joy45@gmail.com 1607730414 7056 Roy Turnpike Belfast England 95070 UK 47 Female Medium Premium null 2023 MAY 12:46:14 7.0 15.96041562 111.72 Books Random House Non-Fiction Bad Standard Debit Card Shipped 1 Travel 2 360

In [0]:
def create_city_sales(df):
    print("Creating city sales analytics...")
    city_sales = df \
        .groupBy("City", "Country") \
        .agg(
            round(sum("Total_Amount"), 2).alias("Total_Sales"),
            count("Transaction_ID").alias("Number_of_Transactions"),
            countDistinct("Customer_ID").alias("Unique_Customers")
        ) \
        .orderBy(desc("Total_Sales"))
    
    # Write to ADLS Gen2
    city_sales.write.format("delta") \
        .mode("overwrite") \
        .save(f"/mnt/silverData/processed-data/city_sales")
    
    print(f"City sales data written to: /mnt/silverData/processed-data/CitySales")
    return city_sales

In [0]:
def create_quarterly_sales(df):
    print("Creating quarterly sales analytics...")
    quarterly_sales = df \
        .groupBy("Year", "Quarter") \
        .agg(
            round(sum("Total_Amount"), 2).alias("Total_Sales"),
            count("Transaction_ID").alias("Number_of_Transactions"),
            avg("Total_Amount").alias("Average_Transaction_Amount")
        ) \
        .orderBy("Year", "Quarter")
    
    # Write to ADLS Gen2
    quarterly_sales.write.format("delta") \
        .mode("overwrite") \
        .save(f"/mnt/silverData/processed-data/quarterly_sales")
    
    print(f"City sales data written to: /mnt/silverData/processed-data/QuarterlySales")
    return quarterly_sales

In [0]:
def create_city_products(df):
    print("Creating city products analytics...")
    city_products = df \
        .groupBy("City", "Country", "Product_Category") \
        .agg(
            sum("Total_Purchases").alias("Total_Products_Sold"),
            round(sum("Total_Amount"), 2).alias("Category_Sales")
        ) \
        .orderBy("City", desc("Total_Products_Sold"))
    
    # Write to ADLS Gen2
    city_products.write.format("delta") \
        .mode("overwrite") \
        .save(f"/mnt/silverData/processed-data/city_products")
    
    print(f"City products data written to: /mnt/silverData/processed-data/CityProducts")
    return city_products

In [0]:
print("Starting cleaned Data transformations...")

city_sales_df = create_city_sales(cleanData_df)
quarterly_sales_df = create_quarterly_sales(cleanData_df)
city_products_df = create_city_products(cleanData_df)

Starting cleaned Data transformations...
Creating city sales analytics...
City sales data written to: /mnt/silverData/processed-data/CitySales
Creating quarterly sales analytics...
City sales data written to: /mnt/silverData/processed-data/QuarterlySales
Creating city products analytics...
City products data written to: /mnt/silverData/processed-data/CityProducts


In [0]:
display(city_sales_df)
display(quarterly_sales_df)
display(city_products_df)

City Country Total_Sales Number_of_Transactions Unique_Customers Chicago USA 2.866436453E7 21080 18732 Portsmouth UK 2.653248393E7 19322 17345 San Francisco USA 1.61487074E7 11940 11162 Frankfurt Germany 1.381088438E7 10080 9516 Boston USA 1.23236123E7 9031 8591 New York USA 7066868.27 5253 5091 Fort Worth USA 6777432.63 4966 4814 Winnipeg Canada 3180379.92 2361 2337 Birmingham UK 3169138.51 2328 2280 Hanover Germany 3167612.34 2256 2228 Plymouth UK 3167405.77 2252 2223 Victoria Canada 3144590.3 2277 2251 Edinburgh UK 3140543.84 2286 2247 Bielefeld Germany 3130123.38 2254 2225 Hobart Australia 3127681.91 2267 2232 Bendigo Australia 3122579.78 2288 2248 Calgary Canada 3119234.57 2256 2228 Cardiff UK 3117239.6 2230 2200 Edmonton Canada 3111863.39 2252 2235 Mackay Australia 3111436.79 2273 2245 Darwin Australia 3106638.88 2229 2196 Wollongong Australia 3095423.46 2211 2181 Brisbane Australia 3094244.8 2246 2216 Brighton UK 3090100.07 2248 2224 Manchester UK 3070991.52 2224 2183 Bremen Germany 3069321.46 2181 2157 Wuppertal Germany 3069041.16 2234 2193 Stuttgart Germany 3065939.61 2214 2180 Perth Australia 3058706.23 2252 2226 Belfast UK 3058036.15 2215 2191 Geelong Australia 3053835.73 2253 2223 Townsville Australia 3053480.99 2203 2166 Toronto Canada 3048350.12 2215 2178 Nuremberg Germany 3039145.27 2217 2182 Leicester UK 3037580.52 2235 2191 Saskatoon Canada 3036031.88 2204 2182 Leeds UK 3035910.19 2237 2206 Southampton UK 3029515.67 2194 2176 Ballarat Australia 3026854.66 2198 2166 Albury-wodonga Australia 3026055.88 2215 2187 Düsseldorf Germany 3019081.15 2210 2177 Oxford UK 3016244.44 2205 2170 London Canada 3012658.6 2235 2206 Ottawa Canada 3009105.81 2158 2135 Liverpool UK 3006955.98 2140 2107 Glasgow UK 3004385.44 2155 2128 Barrie Canada 3002774.87 2208 2178 Kitchener Canada 3002180.36 2187 2158 Adelaide Australia 3000755.15 2199 2168 Sydney Australia 2995422.62 2204 2175 Gold Coast Australia 2994436.74 2124 2100 Nottingham UK 2990708.45 2161 2139 Münster Germany 2978739.13 2174 2150 Canberra Australia 2976056.95 2170 2141 Regina Canada 2968471.94 2190 2161 St. John's Canada 2966945.93 2197 2158 Bochum Germany 2963080.56 2171 2151 London UK 2963066.5 2158 2125 Newcastle Upon Tyne UK 2956157.93 2174 2151 Hull UK 2950738.65 2181 2153 Cairns Australia 2948238.05 2208 2174 Oshawa Canada 2945906.92 2206 2170 Cologne Germany 2938116.29 2133 2105 Duisburg Germany 2934944.87 2167 2140 Kelowna Canada 2932469.38 2161 2126 Hamburg Germany 2932286.38 2142 2104 Hamilton Canada 2924170.73 2157 2137 Launceston Australia 2923214.12 2175 2147 Dortmund Germany 2922304.53 2124 2097 Dresden Germany 2921434.32 2158 2136 Vancouver Canada 2915526.28 2124 2090 Leipzig Germany 2914057.2 2141 2115 Quebec City Canada 2909864.05 2137 2106 Newcastle Australia 2909801.28 2143 2122 Sheffield UK 2905033.87 2172 2149 Montreal Canada 2902145.09 2185 2149 Bonn Germany 2895715.54 2164 2132 Windsor Canada 2890381.9 2084 2054 Halifax Canada 2887851.1 2126 2102 Toowoomba Australia 2884237.82 2170 2145 Berlin Germany 2867749.12 2109 2091 Essen Germany 2864734.57 2133 2111 Bristol UK 2857017.0 2142 2109 Munich Germany 2844782.23 2193 2168 Melbourne Australia 2813449.33 2041 2014 Memphis USA 1292266.57 920 916 San Antonio USA 1282935.09 942 938 Phoenix USA 1268323.4 896 891 Louisville USA 1265835.47 905 901 Dallas USA 1265322.47 872 868 Los Angeles USA 1248019.46 902 899 New Orleans USA 1245852.29 887 885 Houston USA 1242192.45 905 900 Nashville USA 1238764.48 887 880 San Jose USA 1237565.94 863 857 Detroit USA 1223467.29 881 877 Albuquerque USA 1219508.66 881 875 Atlanta USA 1218345.24 866 864 Tulsa USA 1212499.43 867 860 Fresno USA 1210297.84 873 867 Austin USA 1209643.31 932 928 Oakland USA 1209638.14 889 885 Indianapolis USA 1208668.53 904 898 Columbus USA 1205525.77 880 876 Raleigh USA 1203928.15 894 891 Baltimore USA 1201417.17 876 872 Las Vegas USA 1200364.3 894 890 Jacksonville USA 1197024.49 896 891 Milwaukee USA 1196829.79 855 853 Omaha USA 1195970.06 8

Year Quarter Total_Sales Number_of_Transactions Average_Transaction_Amount 2023 1 4.639100595E7 33949 1366.4910881027417 2023 2 1.0989676372E8 80398 1366.909173362524 2023 3 1.0408643914E8 75867 1371.9593385793519 2023 4 7.446298993E7 54562 1364.7408439939861 2024 1 5.256247139E7 38623 1360.9111511275692 2024 2 7222270.81 5255 1374.361714557565 2024 3 5849413.18 4368 1339.151369047619 2024 4 184165.11 145 1270.1042068965517

City Country Product_Category Total_Products_Sold Category_Sales Adelaide Australia Electronics 2950.0 724656.65 Adelaide Australia Home Decor 2523.0 636323.68 Adelaide Australia Books 2237.0 604862.35 Adelaide Australia Grocery 2167.0 525325.56 Adelaide Australia Clothing 2002.0 509586.91 Albuquerque USA Electronics 1087.0 274269.25 Albuquerque USA Grocery 963.0 248655.33 Albuquerque USA Books 927.0 250822.53 Albuquerque USA Clothing 874.0 229182.26 Albuquerque USA Home Decor 787.0 216579.29 Albury-wodonga Australia Electronics 3260.0 812357.06 Albury-wodonga Australia Clothing 2365.0 603139.85 Albury-wodonga Australia Grocery 2203.0 561233.25 Albury-wodonga Australia Home Decor 2078.0 518142.85 Albury-wodonga Australia Books 2072.0 531182.87 Arlington USA Electronics 1147.0 292192.6 Arlington USA Grocery 959.0 258038.1 Arlington USA Books 811.0 198927.41 Arlington USA Home Decor 790.0 226974.31 Arlington USA Clothing 744.0 172258.79 Atlanta USA Electronics 1281.0 342324.72 Atlanta USA Clothing 967.0 229072.12 Atlanta USA Grocery 914.0 229098.24 Atlanta USA Books 848.0 219843.48 Atlanta USA Home Decor 805.0 198006.68 Austin USA Electronics 1303.0 339185.73 Austin USA Books 949.0 235397.42 Austin USA Grocery 900.0 223459.64 Austin USA Home Decor 836.0 195845.6 Austin USA Clothing 797.0 215754.92 Ballarat Australia Electronics 2825.0 727059.58 Ballarat Australia Grocery 2378.0 597043.1 Ballarat Australia Books 2275.0 566882.19 Ballarat Australia Home Decor 2229.0 579260.47 Ballarat Australia Clothing 2171.0 556609.32 Baltimore USA Grocery 1045.0 270881.17 Baltimore USA Electronics 1033.0 235042.67 Baltimore USA Clothing 947.0 251199.09 Baltimore USA Home Decor 857.0 237265.68 Baltimore USA Books 831.0 207028.56 Barrie Canada Electronics 2953.0 752405.92 Barrie Canada Grocery 2467.0 624298.92 Barrie Canada Clothing 2324.0 596908.37 Barrie Canada Books 2166.0 536666.35 Barrie Canada Home Decor 1973.0 492495.31 Belfast UK Electronics 3063.0 776340.54 Belfast UK Grocery 2379.0 593355.88 Belfast UK Clothing 2372.0 609839.66 Belfast UK Home Decor 2145.0 559128.56 Belfast UK Books 1972.0 519371.51 Bendigo Australia Electronics 2851.0 715235.07 Bendigo Australia Grocery 2564.0 655057.77 Bendigo Australia Home Decor 2378.0 588357.6 Bendigo Australia Clothing 2321.0 594609.21 Bendigo Australia Books 2149.0 569320.13 Berlin Germany Electronics 2889.0 738587.4 Berlin Germany Grocery 2272.0 609049.0 Berlin Germany Clothing 2191.0 540410.99 Berlin Germany Home Decor 1953.0 476455.99 Berlin Germany Books 1879.0 503245.74 Bielefeld Germany Electronics 3212.0 846192.75 Bielefeld Germany Books 2293.0 601660.98 Bielefeld Germany Home Decor 2277.0 581356.84 Bielefeld Germany Grocery 2165.0 566591.46 Bielefeld Germany Clothing 2113.0 534321.35 Birmingham UK Electronics 3168.0 811276.81 Birmingham UK Clothing 2490.0 639839.36 Birmingham UK Grocery 2330.0 576049.35 Birmingham UK Books 2243.0 571113.75 Birmingham UK Home Decor 2203.0 570859.24 Bochum Germany Electronics 3023.0 771975.9 Bochum Germany Grocery 2196.0 569409.28 Bochum Germany Books 2144.0 519740.68 Bochum Germany Clothing 2110.0 553595.14 Bochum Germany Home Decor 2093.0 548359.56 Bonn Germany Electronics 2897.0 733363.0 Bonn Germany Books 2333.0 577356.67 Bonn Germany Grocery 2276.0 545221.15 Bonn Germany Clothing 2198.0 554804.29 Bonn Germany Home Decor 2011.0 484970.43 Boston USA Electronics 9903.0 2506370.84 Boston USA Home Decor 9693.0 2484175.47 Boston USA Grocery 9624.0 2454693.56 Boston USA Clothing 9621.0 2455452.86 Boston USA Books 9558.0 2422919.57 Bremen Germany Electronics 3018.0 767557.46 Bremen Germany Clothing 2336.0 569371.48 Bremen Germany Grocery 2245.0 597564.26 Bremen Germany Home Decor 2154.0 559688.17 Bremen Germany Books 2109.0 575140.09 Brighton UK Electronics 3153.0 809742.93 Brighton UK Books 2265.0 591655.8 Brighton UK Home Decor 2263.0 580626.54 Brighton UK Clothing 2242.0 547842.25 Brighton UK Grocery 2191.0 560232.55 Brisbane Australia Electronics 3025.0 79